In [15]:
import json
import os

import datasets

_DESCRIPTION = """
The datasets were collected and published to present the educational level of NC population in different areas. The educational attainment for the black population data can raise concern for the educational equity issue in North Carolina. The combined dataset aims to offer a holistic perspective on educational levels and equity, with a specific focus on the educational attainment of the Black population aged 25 and over.
"""

_HOMEPAGE = "https://huggingface.co/datasets/YXu120/NC_Education"

_LICENSE = "cc-by-sa-4.0"

_URL = "https://drive.google.com/file/d/1Au9xwsnDkRx4TMWwndWKbzLR5u9WXUQZ"

class NCEducationDataset(datasets.GeneratorBasedBuilder):
    VERSION = datasets.Version("1.0.0")

    def _info(self):
        features = datasets.Features(
            {
                "area_name": datasets.Value("string"),
                "area_type": datasets.Value("string"),
                "years": datasets.Sequence(
                    {
                        "year": datasets.Value("string"),
                        "variables": datasets.Sequence(
                            {
                                "variable": datasets.Value("string"),
                                "value": datasets.Value("int"),
                                "value_black": datasets.Value("int"),
                            }
                        ),
                    }
                ),
            }
        )

        return datasets.DatasetInfo(
            description=_DESCRIPTION,
            features=features,
            homepage=_HOMEPAGE,
            license=_LICENSE,
        )

    def _split_generators(self, dl_manager):
        data_file = dl_manager.download(_URL)
        return [
            datasets.SplitGenerator(
                name="train",
                gen_kwargs={
                    "filepath": data_file,
                },
            )
        ]

    def _generate_examples(self, filepath):
        with open(filepath, "r", encoding="utf-8") as file:
            data = json.load(file)
            for idx, (area_name, area_data) in enumerate(data.items()):
                years_data = []
                for year, variables in area_data["years"].items():
                    year_data = {
                        "year": year,
                        "variables": [
                            {
                                "variable": variable["variable"],
                                "value": variable["value"],
                                "value_black": variable.get("value_black"),
                            }
                            for variable in variables
                        ],
                    }
                    years_data.append(year_data)

                yield idx, {
                    "area_name": area_name,
                    "area_type": area_data["area_type"],
                    "years": years_data,
                }